# Pull Google Spreadsheet

In [1]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from pathlib import Path
import requests
import json
from pprint import pprint
from multiprocessing.pool import ThreadPool
import threading
import urllib.request
import difflib
import unidecode

import slugify
from tqdm import tqdm_notebook as tqdm
import pandas as pd
from scipy.io import loadmat
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt

import sys
sys.path.append('/work/megapixels_dev/megapixels')
from app.utils import api_utils, identity_utils
from app.settings import app_cfg
from app.settings import types

## To CSV

In [2]:
# add CASIA Webface

import os
import click
import re
import os
import csv
import string
import codecs
import gspread
from os.path import join
from pathlib import Path
import simplejson as json
from oauth2client.service_account import ServiceAccountCredentials

from app.settings import types
from app.settings import app_cfg

In [3]:
def fetch_spreadsheet():
  """Open the Google Spreadsheet, which contains the individual worksheets"""
  scope = ['https://spreadsheets.google.com/feeds','https://www.googleapis.com/auth/drive']
  fp_creds = join(app_cfg.DIR_ROOT, 'scraper/.creds/Megapixels-ef28f91112a9.json')
  credentials = ServiceAccountCredentials.from_json_keyfile_name(fp_creds, scope)
  docid = "1denb7TjYsN9igHyvYah7fQ0daABW32Z30lwV7QrDJQc"
  client = gspread.authorize(credentials)
  spreadsheet = client.open_by_key(docid)
  return spreadsheet

def fetch_worksheet(name="institutions"):
  """Get a reference to a particular "worksheet" from the Google Spreadsheet"""
  spreadsheet = fetch_spreadsheet()
  return spreadsheet.worksheet(name)

def fetch_google_sheet(name="institutions"):
  """Get all the values from a particular worksheet as a list of lists.
  Returns:
  :keys - the first row of the document
  :lines - a list of lists with the rest of the rows"""
  rows = fetch_worksheet(name).get_all_values()
  keys = rows[0]
  lines = rows[1:]
  return keys, lines

def fetch_google_sheet_objects(name):
  """Get all the values from a worksheet as a list of dictionaries"""
  keys, rows = fetch_google_sheet(name)
  recs = []
  for row in rows:
    rec = {}
    for index, key in enumerate(keys):
      rec[key] = row[index]
    recs.append(rec)
  return recs

def fetch_google_lookup(name, item_key='key'):
  """Get all the values from a worksheet as a dictionary of dictionaries.
  Specify which field you want to use as the dictionary key."""
  keys, rows = fetch_google_sheet(name)
  lookup = {}
  for row in rows:
    rec = {}
    for index, key in enumerate(keys):
      rec[key] = row[index]
    lookup[rec[item_key]] = rec
  return lookup

In [14]:
sheet_datasets = fetch_google_sheet_objects(name='datasets')

In [15]:
sheet_stats = fetch_google_sheet_objects(name='statistics')

In [16]:
sheet_stats[0]

{'key': '10k_US_adult_faces',
 'name': '10K US Adult Faces',
 'berit': 'Y',
 'charlie': '',
 'adam': '',
 'priority': '',
 'wild': 'Y',
 'indoor': '',
 'outdoor': '',
 'cyberspace': 'Y',
 'names': '',
 'downloaded': '',
 'year_start': '',
 'year_end': '',
 'year_published': '2013',
 'ongoing': '',
 'images': '10,168 ',
 'videos': '',
 'faces_unique': '10,168 ',
 'total_faces': '',
 'img_per_person': '',
 'num_cameras': '',
 'faces_persons': '',
 'female': '4362',
 'male': '5806',
 'landmarks': '77 ',
 'width': '',
 'height': '256',
 'color': '',
 'gray': '',
 'derivative_of': '',
 'tags': 'fr',
 'source': 'google',
 'purpose_short': 'US adult faces database',
 'size_gb': '',
 'agreement': '',
 'agree_requied': '',
 'agreement_signed': '',
 'comment': 'Using an online random name generator based on the 1990 U.S. Census name distribution we randomly sampled 25,000 first and last names and automatically downloaded from Google Image Search',
 'comment 2': '',
 'comment 3': '',
 '': ''}

In [13]:
df_datasets.keys()

Index(['', 'added_on', 'comments', 'faces', 'ft_share', 'key', 'name_full',
       'name_short', 'pdf_paper', 'relevance', 'subset_of', 'superset_of',
       'url', 'using'],
      dtype='object')

In [5]:
sheet = fetch_google_lookup(name=opt_spreadsheet)

In [8]:
print(sheet['lfw'])

{'key': 'lfw', 'name_short': 'LFW', 'using': 'Y', 'ft_share': '1', 'subset_of': '', 'superset_of': '', 'name_full': 'Labeled Faces in-the-Wild', 'url': 'http://vis-www.cs.umass.edu/lfw/', 'added_on': '', 'faces': '', 'pdf_paper': 'Y', 'comments': 'many references, only included first on from 2007', '': '', 'relevance': '10'}


In [6]:
for k, v in sheet.items():
  print(k)

10k_US_adult_faces
3d_rma
3dddb_unconstrained
3dpes
4dfab
50_people_one_question
a_pascal_yahoo
aberdeen 
adience
afad
afew_va
affectnet
aflw
afw
agedb
alert_airport
am_fed
apis
ar_facedb
awe_ears
b3d_ac
bbc_pose
berkeley_pose
bfm
bio_id
bjut_3d
bosphorus
bp4d_plus
bp4d_spontanous
brainwash
bu_3dfe
buhmap_db
cafe
caltech_10k_web_faces
caltech_faces
caltech_pedestrians
camel
cas_peal
casablanca
casia_webface
caviar4reid
celeba
celeba_plus
cfd
chalearn
chokepoint
cityscapes
clothing_co_parsing
cmdp
cmu_pie
coco
coco_action
coco_qa
cofw
cohn_kanade
cohn_kanade_plus
columbia_gaze
complex_activities
cuhk01
cuhk02
cuhk03
cvc_01_barcelona
czech_news_agency
d3dfacs
dartmouth_children
data_61
deep_fashion
disfa
distance_nighttime
duke_mtmc
emotio_net
eth_andreas_ess
europersons
expw
face_research_lab
face_scrub
face_tracer
facebook
facebook_100
faceplace
faces94
faces95
faces96
families_in_the_wild
fddb
fei
feret
ferplus
fia
fiw_300
florida_inmates
frav2d
frav3d
grimace
frgc
gallagher
gavab_db
